In [844]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import itertools
import string
import math
import re

In [4]:
medicare_html = requests.get("https://q1medicare.com/PartD-SearchMA-Medicare-2022PlanFinder.php?utm_source=partd&utm_campaign=NavLink&utm_medium=LeftNavi")
medicare_soup = BeautifulSoup(medicare_html.content, "html.parser")
med_links = []
for html_ in medicare_soup.find_all("span", {'class':'text'}):
    med_links.append([l['href'] for l in html_.find_all("a", href=True)])
temp = list(itertools.chain.from_iterable(med_links))
med_links = temp[1:-1]
            

In [5]:
county_links = list()
for link in med_links:
    state_med_url = "https://q1medicare.com/"+link
    state_req = requests.get(state_med_url)
    med_state_soup = BeautifulSoup(state_req.content, "html.parser")
    for county_tbl in med_state_soup.find_all('table', {'class': 'chart'}):
        for row in county_tbl.find_all("tr"):
            c_links = [r.find("a", href=True) for r in row.find_all("td", {'style':'width:15%'})]
            county_links.append([c_link['href'] for c_link in c_links])
full_county_links = list(itertools.chain.from_iterable((county_links)))    

In [6]:
full_plan_names = list()

In [51]:
full_plan_names2 = list()
for i, region in enumerate(full_county_links[2400:]):
    if i%100 == 0:
        print(f'i: {i}')
    try:
        region_req = requests.get(region, timeout=10)
    except requests.exceptions.ConnectionError as e:
        region_req = "No response"
        print(f'No response on interation{i}\n')
        continue
    except requests.exceptions.ConnectTimeout as e:
        print(f'Time out on iteration {i}\n')
        continue
    except requests.exceptions.Timeout as e:
        print(f'Connection pool read timeout on iteration {i}')
        continue
    region_soup = BeautifulSoup(region_req.content, "html.parser")
    curr_tbl = region_soup.find("table", {"class":"chart"})
    if curr_tbl is None:
        print(f'url: {region}\n')
        continue
    full_plan_names2.append([plan_name.get_text(strip=True) for plan_name in curr_tbl.tbody.find_all("a", {"class": "teasertext"})])
full_plan_names_2022 = list(itertools.chain.from_iterable(full_plan_names))
full_plan_names_2022

i: 0
url: https://q1medicare.com/PartD-SearchMA-Medicare-2022PlanFinder.php?state=SD&countyCode=46102&showCounty=Oglala%20Lakota&utm_source=partd&utm_medium=mastatepage&utm_campaign=link2macountyname

Connection pool read timeout on iteration 65
i: 100
i: 200
i: 300
i: 400
i: 500
url: https://q1medicare.com/PartD-SearchMA-Medicare-2022PlanFinder.php?state=VA&countyCode=51850&showCounty=Radford%20City&utm_source=partd&utm_medium=mastatepage&utm_campaign=link2macountyname

url: https://q1medicare.com/PartD-SearchMA-Medicare-2022PlanFinder.php?state=VA&countyCode=51875&showCounty=Salem%20City&utm_source=partd&utm_medium=mastatepage&utm_campaign=link2macountyname

i: 600
i: 700


['Lasso Healthcare Growth (MSA) - H1924-001-0',
 'Lasso Healthcare Growth Plus (MSA) - H1924-004-0',
 'AARP Medicare Advantage Choice (PPO) - H6528-033-0',
 'Browse Formulary',
 'AARP Medicare Advantage Patriot (HMO) - H0432-012-0',
 'AARP Medicare Advantage Plan 1 (HMO) - H0432-003-0',
 'Browse Formulary',
 'AARP Medicare Advantage Plan 3 (HMO) - H2802-041-0',
 'Browse Formulary',
 'Aetna Medicare Eagle Plan (PPO) - H5521-229-0',
 'Aetna Medicare Freedom Plan (PPO) - H5521-224-0',
 'Browse Formulary',
 'Details:',
 'Blue Advantage Complete (PPO) - H0104-012-0',
 'Browse Formulary',
 'Details:',
 'Cigna Fundamental Medicare (HMO) - H4513-045-0',
 'Cigna Preferred AL Medicare (HMO) - H4513-046-1',
 'Browse Formulary',
 'Details:',
 'Cigna Preferred Medicare (HMO) - H4513-057-0',
 'Browse Formulary',
 'Details:',
 'Cigna True Choice Medicare (PPO) - H7849-013-0',
 'Browse Formulary',
 'Details:',
 'Humana Honor (PPO) - H5216-236-0',
 'HumanaChoice H5216-269 (PPO) - H5216-269-0',
 'Browse

In [55]:
all_plan_names = list(itertools.chain.from_iterable(full_plan_names2+full_plan_names))

In [279]:
all_plans = full_plan_names2+full_plan_names

In [277]:
all_plan_names_2022 = list((set(all_plan_names)))

In [265]:
full_plan_names

['Lasso Healthcare Growth (MSA) - H1924-001-0',
 'Lasso Healthcare Growth Plus (MSA) - H1924-004-0',
 'Medica Prime Solution Standard (Cost) - H2450-044-0',
 'Medica Prime Solution Thrift (Cost) - H2450-030-0',
 'Medica Prime Solution Standard w/Rx (Cost) - H2450-049-0',
 'Browse Formulary',
 'Details:',
 'Medica Prime Solution Thrift w/Rx (Cost) - H2450-007-0',
 'Browse Formulary',
 'Details:',
 'Medica Prime Solution Core (Cost) - H2450-034-0',
 'Medica Prime Solution Core w/Rx (Cost) - H2450-035-0',
 'Browse Formulary',
 'Details:',
 'Medica Prime Solution Premier (Cost) - H2450-036-0',
 'Medica Prime Solution Premier w/Rx (Cost) - H2450-037-0',
 'Browse Formulary',
 'Details:',
 'Lasso Healthcare Growth (MSA) - H1924-001-0',
 'Lasso Healthcare Growth Plus (MSA) - H1924-004-0',
 'Medica Prime Solution Standard (Cost) - H2450-044-0',
 'Blue Medicare Advantage PPO (PPO) - H5900-003-0',
 'Browse Formulary',
 'Details:',
 'Medica Prime Solution Thrift (Cost) - H2450-030-0',
 'UnitedHeal

In [313]:
with open('medicare_plans.txt', 'w') as f:
    for line in set([j for i in all_plan_names_2022 for j in i.split(" ")]):
        f.write(f"{line}\n")


In [840]:
lower_upper_hcpcs = []
for e in set([j for i in all_plan_names_2022 for j in i.split(" ")]):
    lower_upper_hcpcs.append(e)
    lower_upper_hcpcs.append(e.lower())
with open('medicare_plans_upper_lower.txt', 'w') as f:
    for line in lower_upper_hcpcs:
        f.write(f"{line}\n")


In [17]:
cpt_html = requests.get("https://www.aapc.com/codes/cpt-codes-range/")
cpt_soup = BeautifulSoup(cpt_html.content)
cpt_ranges = list()
for code in cpt_soup.find_all('div', {'class': 'col-md-4'}):
    cpt_ranges.append(code.get_text(strip=True))
cpt_ranges.remove('CODE RANGE')

In [18]:
cpt_codes_by_range = {}
code_list = list()

for cpt_ in cpt_ranges:
    cpt_url = "https://www.aapc.com/codes/cpt-codes-range/" + cpt_
    current_cpt = requests.get(cpt_url)
    current_cpt_soup = BeautifulSoup(current_cpt.content)
    try:
        n = int([x.get_text(strip=True) for x in current_cpt_soup.find('div', {'class': 'col-md-12 pgbox'})][5])
        x = math.ceil(n/10)*10
    except IndexError:
        n = 1
    if n > 1:
        for n in range(0, x+1, 10):
            if n == 0:               
                for current_code in current_cpt_soup.find_all('div', {'class': 'col-md-4'}):
                    code_list.append(current_code.get_text(strip=True))
            else:
                cpt_url = "https://www.aapc.com/codes/cpt-codes-range/" + cpt_ + '/' + str(n)
                current_cpt = requests.get(cpt_url)
                current_cpt_soup = BeautifulSoup(current_cpt.content)
                for current_code in current_cpt_soup.find_all('div', {'class': 'col-md-4'}):
                    code_list.append(current_code.get_text(strip=True))
    else:
        for current_code in current_cpt_soup.find_all('div', {'class': 'col-md-4'}):
            code_list.append(current_code.get_text(strip=True))
                  
    cpt_codes_by_range[cpt_] = code_list
    code_list = []
    
removed_codes_1 = cpt_codes_by_range.pop('0001U-0354U')
remove_codes_2 = cpt_codes_by_range.pop('0002M-0018M')
cpt_codes_by_range  

{'00100-01999': ['00100-00222',
  '00300-00352',
  '00400-00474',
  '00500-00580',
  '00600-00670',
  '00700-00797',
  '00800-00882',
  '00902-00952',
  '01112-01173',
  '01200-01274',
  '01320-01444',
  '01462-01522',
  '01610-01680',
  '01710-01782',
  '01810-01860',
  '01916-01942',
  '01951-01953',
  '01958-01969',
  '01990-01999'],
 '10004-69990': ['10004-10021',
  '10030-19499',
  '20100-29999',
  '30000-32999',
  '33016-37799',
  '38100-38999',
  '39000-39599',
  '40490-49999',
  '50010-53899',
  '54000-55899',
  '55920-55920',
  '55970-55980',
  '56405-58999',
  '59000-59899',
  '60000-60699',
  '61000-64999',
  '65091-68899',
  '69000-69979',
  '69990-69990'],
 '70010-79999': ['70010-76499',
  '76506-76999',
  '77001-77022',
  '77046-77067',
  '77071-77092',
  '77261-77799',
  '78012-79999'],
 '80047-89398': ['80047-80081',
  '80143-80377',
  '80400-80439',
  '80503-80506',
  '81000-81099',
  '81105-81479',
  '81410-81471',
  '81490-81599',
  '82009-84999',
  '85002-85999',
  

In [19]:
headers = []
curr_codes = []
full_cpt_codes = []
for cpt_range in cpt_codes_by_range.keys():
    for sub_range in cpt_codes_by_range[cpt_range]:
        sub_range_url = "https://www.aapc.com/codes/cpt-codes-range/" + sub_range
        current_cpt_range = requests.get(sub_range_url)
        current_cpt_soup = BeautifulSoup(current_cpt_range.content)
        headers.append(current_cpt_soup.find('div', {'class': 'cpt-orange'}).get_text(strip=True))
        try:
            if current_cpt_soup.find('div', {'class': 'col-md-12 pgbox'}) is None:
                continue
            else:
                n = int(current_cpt_soup.find('div', {'class': 'col-md-12 pgbox'}).get_text(" ",strip=True).split()[5])
                x = math.ceil(n/10)*10
        except IndexError:
            n = 1
        if n > 1:
            for _ in range(0, x+1, 10):
                if _ == 0:
                    for _ in current_cpt_soup.find_all('div', {'class': 'col-md-4'}):
                        if 'Showing' in _.get_text(",", strip=True).split(','):
                            index = _.get_text(",", strip=True).split(',').index("Showing")
                            full_cpt_codes.append(_.get_text(",", strip=True).split(',')[:index])
                        else:
                            full_cpt_codes.append(_.get_text(",", strip=True).split(','))
                else:
                    sub_range_url = "https://www.aapc.com/codes/cpt-codes-range/"+sub_range+"/"+str(_) 
                    current_cpt_range = requests.get(sub_range_url)
                    current_cpt_soup = BeautifulSoup(current_cpt_range.content)
                    for _ in current_cpt_soup.find_all('div', {'class': 'col-md-4'}):
                        if 'Showing' in _.get_text(",", strip=True).split(','):
                            index = _.get_text(",", strip=True).split(',').index("Showing")
                            full_cpt_codes.append(_.get_text(",", strip=True).split(',')[:index])
                        else:
                            full_cpt_codes.append(_.get_text(",", strip=True).split(','))
                        
        else:
            for _ in current_cpt_soup.find_all('div', {'class': 'col-md-4'}):
                full_cpt_codes.append(_.get_text(",", strip=True).split(','))
full_cpt_codes  
           

[['00100',
  '00102',
  '00103',
  '00104',
  '00120',
  '00124',
  '00126',
  '00140',
  '00142',
  '00144'],
 ['00145',
  '00147',
  '00148',
  '00160',
  '00162',
  '00164',
  '00170',
  '00172',
  '00174',
  '00176'],
 ['00190',
  '00192',
  '00210',
  '00211',
  '00212',
  '00214',
  '00215',
  '00216',
  '00218',
  '00220'],
 ['00222'],
 ['00300', '00320', '00322', '00326', '00350', '00352'],
 ['00400',
  '00402',
  '00404',
  '00406',
  '00410',
  '00450',
  '00454',
  '00470',
  '00472',
  '00474'],
 ['00500',
  '00520',
  '00522',
  '00524',
  '00528',
  '00529',
  '00530',
  '00532',
  '00534',
  '00537'],
 ['00539',
  '00540',
  '00541',
  '00542',
  '00546',
  '00548',
  '00550',
  '00560',
  '00561',
  '00562'],
 ['00563', '00566', '00567', '00580'],
 ['00600',
  '00604',
  '00620',
  '00625',
  '00626',
  '00630',
  '00632',
  '00635',
  '00640',
  '00670'],
 ['00700',
  '00702',
  '00730',
  '00731',
  '00732',
  '00750',
  '00752',
  '00754',
  '00756',
  '00770'],
 ['0

In [20]:
cpt_codes = list(itertools.chain.from_iterable(full_cpt_codes))

In [323]:
cpt_df = pd.DataFrame(cpt_codes, columns = ["CPT Code"])
cpt_codes

['00100',
 '00102',
 '00103',
 '00104',
 '00120',
 '00124',
 '00126',
 '00140',
 '00142',
 '00144',
 '00145',
 '00147',
 '00148',
 '00160',
 '00162',
 '00164',
 '00170',
 '00172',
 '00174',
 '00176',
 '00190',
 '00192',
 '00210',
 '00211',
 '00212',
 '00214',
 '00215',
 '00216',
 '00218',
 '00220',
 '00222',
 '00300',
 '00320',
 '00322',
 '00326',
 '00350',
 '00352',
 '00400',
 '00402',
 '00404',
 '00406',
 '00410',
 '00450',
 '00454',
 '00470',
 '00472',
 '00474',
 '00500',
 '00520',
 '00522',
 '00524',
 '00528',
 '00529',
 '00530',
 '00532',
 '00534',
 '00537',
 '00539',
 '00540',
 '00541',
 '00542',
 '00546',
 '00548',
 '00550',
 '00560',
 '00561',
 '00562',
 '00563',
 '00566',
 '00567',
 '00580',
 '00600',
 '00604',
 '00620',
 '00625',
 '00626',
 '00630',
 '00632',
 '00635',
 '00640',
 '00670',
 '00700',
 '00702',
 '00730',
 '00731',
 '00732',
 '00750',
 '00752',
 '00754',
 '00756',
 '00770',
 '00790',
 '00792',
 '00794',
 '00796',
 '00797',
 '00800',
 '00802',
 '00811',
 '00812',


In [337]:
with open('cpt_codes.txt', 'w') as f:
    for line in cpt_codes:
        f.write(f"{line}\n")

In [836]:
[f"{y}{'U'}" for y in removed_codes_1[0].split("U")[0:-1]] + [f"{x}{'M'}" for x in remove_codes_2[0].split("M")[0:-1]]

['0001U',
 '0002U',
 '0003U',
 '0005U',
 '0007U',
 '0008U',
 '0009U',
 '0010U',
 '0011U',
 '0016U',
 '0002M',
 '0003M',
 '0004M',
 '0006M',
 '0007M',
 '0011M',
 '0012M',
 '0013M',
 '0014M',
 '0015M']

In [852]:
removed_terms = [f"{elem}{'U'}" for elem in list(itertools.chain.from_iterable([elem.split("U")[1:-1] for elem in removed_codes_1]))]+[f"{elem}{'M'}" for elem in list(itertools.chain.from_iterable([elem.split("M")[1:-1] for elem in remove_codes_2]))]
all_cpt_codes = cpt_codes+removed_terms
cpt_upper_lower = []
for _ in all_cpt_codes:
    if re.search('[a-zA-Z]',_):
        cpt_upper_lower.append(_)
        cpt_upper_lower.append(_.lower())
    else:
        cpt_upper_lower.append(_)
cpt_upper_lower

with open('cpt_codes_upper_lower.txt', 'w') as f:
      for line in cpt_upper_lower:
             f.write(f"{line}\n")

In [22]:
med_html = requests.get("https://www.medicareadvantage.com/plans-by-state")
med_soup = BeautifulSoup(med_html.content, "html.parser")
states = []
for url_link in med_soup.find_all("a", href=True):
    if "plans-by-state/" in url_link['href']:
        states.append(url_link['href'].split('/')[2])

In [23]:
all_states = list(set(states))

In [24]:
state_counties = {}
for state in all_states:
    county_url = "https://www.medicareadvantage.com/plans-by-state/" + state
    county = requests.get(county_url)
    county_soup = BeautifulSoup(county.content, "html.parser")
    current_county = []
    for county in county_soup.find_all("a", href=True):
        if "/plans-by-state/" in county['href'] and '/part-d/plans-by-state/' not in county['href']:
            current_county.append(county['href'].split('/')[3])
            
    state_counties[state] = current_county
    current_county = []


In [25]:
all_medcare_data = []
for state in state_counties.keys():
    for county in state_counties[state]:
        med_url = "https://www.medicareadvantage.com/plans-by-state/" + state + "/" + county
        try:
            med_html = requests.get(med_url, timeout=7)
        except requests.exceptions.ConnectionError as e:
            med_html = "No response"
            continue
        med_soup = BeautifulSoup(med_html.content, "html.parser")
        tbl = (med_soup.find('div', {'class': 'county-listings'}))
        if tbl:
            table_row = [x.get_text(",", strip=True).split(',') for x in tbl.tbody.find_all('tr')]
        else:
            continue
        all_medcare_data.append(table_row)
    
        
all_medcare_data


[[['AARP Medicare Advantage Choice (PPO)',
   'H2228-120-000',
   '$28',
   '$0',
   '$5700',
   'Yes',
   '4 out of 5 stars'],
  ['AARP Medicare Advantage Patriot (PPO)',
   'H2228-121-000',
   '$0',
   'N/A',
   '$6700',
   'No',
   '4 out of 5 stars'],
  ['Kaiser Permanente Senior Advantage Hawaii Island (HMO)',
   'H1230-014-000',
   '$183',
   '$0',
   '$5100',
   'Yes',
   '5 out of 5 stars'],
  ['UnitedHealthcare Dual Complete (PPO D-SNP)',
   'H2228-043-000',
   '$0',
   '$0',
   '$0',
   'Yes',
   '4 out of 5 stars'],
  ["Wellcare 'Ohana Assist Open (PPO)",
   'H6605-003-000',
   '$14.2',
   '$505',
   '$5000',
   'Yes',
   'Plan too new to be measured'],
  ["Wellcare 'Ohana Dual Liberty (HMO D-SNP)",
   'H2491-004-000',
   '$0',
   '$0',
   '$0',
   'Yes',
   '3.5 out of 5 stars'],
  ["Wellcare 'Ohana No Premium (HMO)",
   'H2491-015-000',
   '$0',
   '$200',
   '$6700',
   'Yes',
   '3.5 out of 5 stars'],
  ["Wellcare 'Ohana Patriot Giveback Open (PPO)",
   'H6605-002-000',


In [26]:
med_html = requests.get("https://www.medicareadvantage.com/plans-by-state/oregon/baker", timeout=7)
med_soup = BeautifulSoup(med_html.content, "html.parser")
med_tbl = (med_soup.find('div', {'class': 'county-listings'}))
med_header = [x.get_text(",", strip=True) for x in med_tbl.find_all('th')]
med_header

['Plan Name',
 'Plan Code',
 'Monthly Premium',
 'Deductible',
 'Out of Pocket Max',
 'Prescription Drug Coverage',
 'Medicare Star Rating']

In [316]:
medcare_flattened_2023 = list(itertools.chain.from_iterable(all_medcare_data))


In [28]:
med_df = pd.DataFrame(medcare_flattened_2023).drop([7,8], axis = 1)
med_df.columns = med_header
med_df

Plan Name      Plan Code  \
0                   AARP Medicare Advantage Choice (PPO)  H2228-120-000   
1                  AARP Medicare Advantage Patriot (PPO)  H2228-121-000   
2      Kaiser Permanente Senior Advantage Hawaii Isla...  H1230-014-000   
3             UnitedHealthcare Dual Complete (PPO D-SNP)  H2228-043-000   
4                      Wellcare 'Ohana Assist Open (PPO)  H6605-003-000   
...                                                  ...            ...   
82331                         Wellcare Assist Open (PPO)  H6594-004-000   
82332                       Wellcare Giveback Open (PPO)  H6594-002-000   
82333                          Wellcare No Premium (HMO)  H1862-001-000   
82334                     Wellcare No Premium Open (PPO)  H6594-001-000   
82335                           Wellcare Plus Open (PPO)  H6594-003-000   

      Monthly Premium Deductible Out of Pocket Max Prescription Drug Coverage  \
0                 $28         $0             $5700                        Yes   
1                  $0        N/A             $6700                         No   
2                $183         $0             $5100                        Yes   
3                  $0         $0                $0                        Yes   
4               $14.2       $505             $5000                        Yes   
...               ...        ...               ...                        ...   
82331           $13.1       $505             $6000                        Yes   
82332              $0         $0             $7550                        Yes   
82333              $0         $0             $6500                        Yes   
82334              $0         $0             $6500                        Yes   
82335           $17.3       $380             $8300                        Yes   

              Medicare Star Rating  
0                 4 out of 5 stars  
1                 4 out of 5 stars  
2                 5 out of 5 stars  
3                 4 out of 5 stars  
4      Plan too new to be measured  
...                            ...  
82331             3 out of 5 stars  
82332             3 out of 5 stars  
82333    Not enough data available  
82334             3 out of 5 stars  
82335             3 out of 5 stars  

[82336 rows x 7 columns]

In [29]:
set([j for i in med_df['Plan Name'].str.split(' ').to_list() for j in i])

{'$1500',
 "'Ohana",
 '(HMO',
 '(HMO)',
 '(HMO-POS',
 '(HMO-POS)',
 '(PFFS)',
 '(PPO',
 '(PPO)',
 '(Regional',
 '+',
 '-',
 '001',
 '1',
 '10',
 '129',
 '2',
 '20',
 '3',
 '30',
 '4',
 '40',
 '5',
 '6',
 '7',
 '8',
 'AARP',
 'AL',
 'AVA',
 'Access',
 'Achieve',
 'Adv',
 'Advantage',
 'Advantra',
 'Advocate',
 'Aetna',
 'Aid',
 'Alabama',
 'Alam.',
 'Alameda',
 'Align',
 'Alignment',
 'AllCare',
 'Alliance',
 'Allina',
 'Ally',
 'Alphonsus',
 'Amber',
 'Amerivantage',
 'Anchor',
 'Anthem',
 'Antonio',
 'Arizona',
 'Ascension',
 'Assist',
 'Assure',
 'Austin',
 'BCN',
 'BEWELL',
 'BR',
 'Back',
 'Balance',
 'Balt',
 'Basic',
 'Baton',
 'Beach',
 'Beaver',
 'Best',
 'Better',
 'Blue',
 'Bonus',
 'Boost',
 'Bronze',
 'Broward',
 'Butler',
 'C-SNP)',
 'CHOICE',
 'COPD',
 'CORE',
 'CalPlus',
 'Canopy',
 'Care',
 'CareBreeze',
 'CareComplete',
 'CareFree',
 'CareNeeds',
 'CareOne',
 'CareSalute',
 'Cares',
 'Carmel',
 'Carolina',
 'Cash',
 'Centennial',
 'Central',
 'Choice',
 'Christi',
 'Ch

In [34]:
req = requests.get("https://www.hcpcsdata.com/Codes")
letter_soup = BeautifulSoup(req.content, "html.parser")
letter_soup.find("table", {'class':'table table-hover'})
letters = [letter.get_text().split()[0][1] for letter in letter_soup.tbody.find_all("tr")]


In [35]:
hcpcs_html = requests.get("https://www.hcpcsdata.com/Codes/A")
hcpcs_soup = BeautifulSoup(hcpcs_html.content, "html.parser")
hcpcs_tbl_html = hcpcs_soup.find("table", {'class':'table table-hover'})
hcpcs_headers = [header.get_text() for header in hcpcs_tbl_html.find_all("th")]


In [331]:
all_hcpcs_rows = []
for letter in letters:
    url = "https://www.hcpcsdata.com/Codes/"+str(letter)
    hcpcs_html = requests.get(url)
    hcpcs_soup = BeautifulSoup(hcpcs_html.content, "html.parser")
    row_data = [x.get_text().split() for x in hcpcs_soup.tbody.find_all('tr')]
    for row in row_data:
        all_hcpcs_rows.append([row[0].lower()] + [" ".join(row[1:]).lower()])


In [335]:
hcpcs_df = pd.DataFrame(all_hcpcs_rows, columns = hcpcs_headers)


Code                                                       a0021
Description    ambulance service, outside state per mile, tra...
Name: 0, dtype: object

In [871]:
hcpcs_codes_only = [x[0] for x in all_hcpcs_rows]
hcpcs_descriptions = [x[1] for x in all_hcpcs_rows]
hcpcs_codes_descriptions = []
for i,j in zip(hcpcs_codes_only, hcpcs_descriptions):
    hcpcs_codes_descriptions.append(i)
    hcpcs_codes_descriptions.append(j)
with open('hcpcs_codes_descriptions', 'w') as f:
    for line in hcpcs_codes_descriptions:
        f.write(f"{line}\n")
    
    

In [870]:
with open('hcpcs_descriptions.txt', 'w') as f:
    for line in set(hcpcs_descriptions):
        f.write(f"{line}\n")

In [38]:
irs_html = requests.get("https://www.irs.gov/forms-instructions-and-publications")
irs_soup = BeautifulSoup(irs_html.content, "html.parser")
irs_tbl = irs_soup.find("table", {'class':"tablesaw tablesaw-stack table table-hover table-striped pup-table"})
irs_headers = [header.get_text() for header in irs_tbl.find_all("th")]


In [377]:
all_irs_rows = []
for i in range(15):
    irs_url = "https://www.irs.gov/forms-instructions-and-publications?items_per_page=200&find=&page=" + str(i)
    irs_html = requests.get(irs_url)
    irs_soup = BeautifulSoup(irs_html.content, "html.parser")
    irs_soup.find("table", {'class':"tablesaw tablesaw-stack table table-hover table-striped pup-table"})
    irs_row_data = [x.get_text().lower() for x in irs_soup.find_all('tr')][1:]
    irs_row_data_filtered = [elem.strip().split('\n') for elem in irs_row_data]
    all_irs_rows.append(irs_row_data_filtered)
    
flat_irs_list = list(itertools.chain.from_iterable(all_irs_rows)) 

In [882]:
#irs_df = pd.DataFrame(flat_irs_list, columns = irs_headers)
irs_form_names = [y[0].strip() for y in flat_irs_list]
irs_form_descriptions = [y[1].strip() for y in flat_irs_list]
all_irs_forms_descriptions = []
for i, j in zip(irs_form_names, irs_form_descriptions):
    all_irs_forms_descriptions.append(i)
    all_irs_forms_descriptions.append(j)
with open('irs_forms_descriptions', 'w') as f:
    for line in all_irs_forms_descriptions:
        f.write(f"{line}\n")

In [953]:
with open('irs_form_descriptions.txt', 'w') as f:
    for line in irs_form_descriptions:
        f.write(f"{line}\n")

In [41]:
alphabet = list(string.ascii_lowercase)
spanish_terms = requests.get("https://www.medicalspanish.com/dictionary/english-spanish/a.html")
spanish_term_soup = BeautifulSoup(spanish_terms.content, "html.parser")
spanish_terms_data = []
for _ in alphabet:
    spanish_url = "https://www.medicalspanish.com/dictionary/english-spanish/"+_+".html"
    spanish_terms = requests.get(spanish_url)
    spanish_term_soup = BeautifulSoup(spanish_terms.content, "html.parser")
    for term in spanish_term_soup.find_all("dd"):
        spanish_terms_data.append(term.get_text(strip=True).split(" "))

In [42]:
span_terms_1 = set([word.replace(",", "") for word in set(list(itertools.chain.from_iterable(spanish_terms_data)))][1:])

In [43]:
span_url = 'https://commongroundinternational.com/medical-spanish/names-of-medical-professions-in-spanish/'
span_terms = requests.get(span_url)
span_soup = BeautifulSoup(span_terms.content, 'html.parser')
span_terms_data = []
for t in span_soup.find('div', {'class':'eight wide column'}):
    span_terms_data.append(t.get_text(" ", strip=True))

In [44]:
span_terms_2 = set([t for t in [term.split() for term in span_terms_data[1:]][0] if t != 'de' and t != 'el' and t != 'la' and t != ','])
span_terms_2.remove('(de')

In [45]:
all_spanish_terms = span_terms_1.symmetric_difference(span_terms_2)
all_spanish_terms

{'parto',
 'médula',
 'abuso',
 'protuberancia',
 'histerectomía',
 'hipoglucemia',
 'geriátrico',
 'compañía',
 'diluida',
 'luz',
 'erupción',
 'locura',
 'parapléjico',
 'orinal',
 'asma',
 'paterna',
 'atrofiarse',
 'lisiar',
 'receta',
 'amargo',
 'distenderse',
 'articulación',
 'bostezar',
 'mejorar',
 'dolores',
 'congestionado',
 'narcotraficante',
 'caspa',
 'plasma',
 'grueso',
 'extremidad',
 'veneno',
 'gingivitis',
 'inyección',
 'ventilador',
 'mastectomía',
 'defibrilador',
 'cuarto',
 'plaga',
 'peligroso',
 'religioso',
 'infancia',
 'lesbiana',
 'baja',
 'choque',
 'sabor',
 'dar',
 'piel',
 'hipo',
 'fuerte',
 'bocio',
 'escorbuto',
 'abdominal',
 'esponja',
 'delgada',
 'materno',
 'vitales',
 'linfáticos',
 'adulta',
 'tranquila',
 'revisar',
 'serpiente',
 'huevo',
 'mortalidad',
 'tóxica',
 'insecto',
 'aviso',
 'horario',
 'crural',
 'cultivo',
 'escuálida',
 'ingle',
 'distender',
 'trauma',
 'desorientación',
 'visita',
 'placenta',
 'doler',
 'recetar',
 'en

In [322]:
with open('spanish_medical_terms.txt', 'w') as f:
    for line in all_spanish_terms:
        f.write(f"{line}\n")

In [46]:
cpap_url = "https://buyersguide.hme-business.com/category/sleep-therapy/cpaps"
cpap_req = requests.get(cpap_url)
cpap_soup = BeautifulSoup(cpap_req.content, 'html.parser')
cpap_vendors = []
for vendor in cpap_soup.find_all('div', {'class':'mainbody'}):
    cpap_vendors.append([v.get_text(strip=True) for v in vendor.find_all("div" , {'class', 'media-heading'})])

In [47]:
list(itertools.chain.from_iterable([c for c in cpap_vendors[1:len(cpap_vendors)-1]]))

['Medical Supply Depot',
 'SnuggleHose LLC',
 'Breas Medical, Inc',
 'CPAP Supply USA',
 'Apex Medical USA Corp',
 'CPAP Supplies Plus',
 '3B Medical, Inc.',
 'Procare Home Medical',
 'Medquarters, Inc',
 'Sunset Healthcare Solutions']

In [235]:
rx_bin_url = "https://q1medicare.com/news/Article.php?article_id=941&category_id=23"
rx_bin_req = requests.get(rx_bin_url)
rx_soup = BeautifulSoup(rx_bin_req.content, 'html.parser')
rx_bin_data = []
headers = []
for i, rx_link in enumerate([rx_['href'] for rx_ in rx_soup.find_all("a", {'class':'textred'}, href=True)][2:12]):
    rx_bin_req = requests.get(rx_link)
    curr_bin = BeautifulSoup(rx_bin_req.content, 'html.parser')
    curr_tbl = curr_bin.find("table", {'class':'chart tbllight'})
    if i == 0:
        rx_headers = [row.get_text(",", strip=True).split(",") for row in curr_tbl.tbody.find_all("tr")][1]
    else:
        rx_bin_data.append([row.get_text(" ",strip=True).split()[-2] for row in curr_tbl.tbody.find_all("tr")][2:])


In [236]:
full_rx_bins = list(itertools.chain.from_iterable(rx_bin_data))

In [238]:
pd.DataFrame(full_rx_bins, columns = [rx_headers[3]])

BIN
0     015574
1     610502
2     016110
3     003858
4     004336
...      ...
1680  020115
1681  012353
1682  610011
1683  012312
1684  610602

[1685 rows x 1 columns]

In [318]:
clinic_url = 'https://www.medicarelist.com/mental-health-clinics/tn/?page='

med_centers = []
for i in range(1, 109):
    clinic_req = requests.get(f'{clinic_url}{i}')
    clinic_soup = BeautifulSoup(clinic_req.content, 'html.parser')
    for clinic in clinic_soup.find_all("table"):
        med_centers.append([c.get_text().lower() for c in clinic.find_all("a", href=True)])


In [321]:
list(itertools.chain.from_iterable(med_centers))

['the heartwork center',
 'wade harvest ministries',
 'counseling center',
 'exemplary behavior',
 'shera thiele',
 'george ruccio',
 'healing oasis therapy, llc',
 'prentiss counseling and consulting pllc',
 'redemption counseling services, llc',
 'better life therapies, llc',
 'centerstone of tennessee inc',
 'saved community services inc',
 'jonathan adair',
 "let's talk therapy at antioch, llc",
 'melissa k hammel',
 'superior residential solutions, llc',
 'midsouth behavior clinic',
 'west tennessee resource center',
 'wright therapy services',
 'stepping stones consulting, llc',
 'starr regional medical center',
 'mindful health and healing therapy services pllc',
 'daystar counseling center',
 'love without walls mental health center',
 'psychiatric services of east tennessee',
 'positive impact behavioral services',
 'quality care support & counseling llc',
 'amway',
 'components of therapy, llc',
 'clover counseling services inc',
 'west tn neurology clinic pllc',
 'youth vill

In [647]:
med_terms_url = 'https://www.medicinenet.com/script/main/alphaidx.asp?p='
med_terms = []
for let in alphabet:
    med_terms_req = requests.get(f'{med_terms_url}{let}_dict')
    med_terms_soup = BeautifulSoup(med_terms_req.content)
    for m in med_terms_soup.find_all("div", {"class": "AZ_results"}):
        for elem in m.find_all("a", href=True):
            med_terms.append(elem.get_text())


In [658]:
#'Immune' in med_terms_a_z
all_medical_terms = [m_term.lower() for m_term in med_terms]

In [669]:
all_medical_terms

['aa-ab',
 'ac-ac',
 'ad-ad',
 'ae-ag',
 'ah-al',
 'am-am',
 'an-an',
 'ao-ap',
 'aq-ar',
 'as-as',
 'at-at',
 'au-au',
 'av-az',
 'a (adenine)',
 'a-',
 'a-t',
 'a.c.',
 'aaa',
 'aaas',
 'aad',
 'aafp (american academy of family physicians)',
 'aamc (ass am medical colleges)',
 'aanat',
 'aao',
 'aaos (american academy of orthopaedic surgeons)',
 'aap',
 'aarskog syndrome',
 'aarskog-scott syndrome',
 'aase-smith syndrome i',
 'aase-smith syndrome ii',
 'ab ovo',
 'ab-',
 'abate',
 'abatement',
 'abdomen',
 'abdomen, acute',
 'abdominal',
 'abdominal aneurysm',
 'abdominal aorta',
 'abdominal aortic aneurysm',
 'abdominal cavity',
 'abdominal guarding',
 'abdominal hysterectomy',
 'abdominal muscle deficiency syndrome',
 'abdominal muscles',
 'abdominal pain',
 'abducent nerve',
 'abduction',
 'abductor muscle',
 'aberration',
 'aberrometry and wavefront imaging',
 'abg (arterial blood gas)',
 'abiological',
 'abiotic',
 'abiotrophy',
 'ablate',
 'ablation',
 'ablation, endometrial',


In [660]:
with open('medical_terms.txt', 'w') as f:
    for line in all_medical_terms:
        f.write(f"{line}\n")

In [705]:
ins_url = 'https://www.rabyintegrativemedicine.com/about/raby-institute-team/integrative-medicine-providers'
ins_url_req = requests.get(f'{ins_url}')
ins_soup = BeautifulSoup(ins_url_req.content)
people_subset = [person.get_text().strip() for person in ins_soup.find_all("h3")][1:-2]

In [713]:
[person.lower().split(',')[0] for person in people_subset]

['theri griego raby',
 'victoria buchanan',
 'katherine a. thurer',
 'karen johnson',
 'stephanie baubie',
 'kathryn willis',
 'mallory przybylinski',
 'katherine chavez (lik)',
 'michelle goebel-angel',
 'tony zayner',
 'tracee blackburn']

In [ ]:
with open('raby_integrative_medicine.txt', 'w') as f:
    for line in all_medical_terms:
        f.write(f"{line}\n")

In [748]:
health_wellness_url = 'https://www.walgreens.com/store/store/brands/brand.jsp?alphabet='
added_url = '&N=300000'
caps_alphabet = list(string.ascii_uppercase)
caps_alphabet.append('0')
health_wellness_brands = []
for cap_let in caps_alphabet:
    health_well_req = requests.get(f'{health_wellness_url}{cap_let}{added_url}')
    health_well_soup = BeautifulSoup(health_well_req.content)
    health_brands = [item.get_text(",", strip=True).split(",") for item in (health_well_soup.find_all("ul", {'class':"row brandslist"}))]
    health_wellness_brands.append(health_brands)
full_brands = list(itertools.chain.from_iterable(health_wellness_brands))

In [757]:
#full_health_brands = list(itertools.chain.from_iterable(full_brands))
full_health_brands = [x.lower() for x in list(itertools.chain.from_iterable(full_brands))]
with open('health_wellness_brands.txt', 'w') as f:
    for line in full_health_brands:
        f.write(f"{line}\n")

In [900]:
antibody_url = 'https://ximbio.com/search?product_type%5Bmonoclonal_antibodies%5D=Monoclonal+Antibodies&page='
add_to_url = '&tab=products'
antibodies = []
for j in range(206):
    antibody_req = requests.get(f'{antibody_url}{j}{add_to_url}')
    antibody_soup = BeautifulSoup(antibody_req.content)
    antibody_tbl = antibody_soup.find("div", {'class' : 'col9 two-thirds-medium omega'})
    for name in antibody_tbl.find_all("a", {'itemprop':"name"}):
            antibodies.append(name.get_text(strip=True))


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205


['Anti-porcine thermal-stable blood protein (TSBP) (90 kDa) [19C5E10] monoclonal antibody',
 'Anti-Polycystin-1 (human) [7.00E+12] monoclonal antibody',
 'Anti-Integrin aVb6 [AvB6 53a.2]',
 'Anti-Cytochrome P450 1B1 [V96]',
 'Anti-Filamentous phage-M13 G8P [9E7] monoclonal antibody',
 'Anti-Oct-1 [YL15]',
 'Anti-TNC-C [4H7.1] monoclonal antibody',
 'Anti-Transmembrane protein [3B5/D7]',
 'Anti-Growth Differentiation Factor 9 [53/1]',
 'Anti-BHMT [3E7]',
 'Anti-porcine thermal-stable blood protein (TSBP) (90 kDa) [19C5E10] monoclonal antibody',
 'Anti-Polycystin-1 (human) [7.00E+12] monoclonal antibody',
 'Anti-Integrin aVb6 [AvB6 53a.2]',
 'Anti-Cytochrome P450 1B1 [V96]',
 'Anti-Filamentous phage-M13 G8P [9E7] monoclonal antibody',
 'Anti-Oct-1 [YL15]',
 'Anti-TNC-C [4H7.1] monoclonal antibody',
 'Anti-Transmembrane protein [3B5/D7]',
 'Anti-Growth Differentiation Factor 9 [53/1]',
 'Anti-BHMT [3E7]',
 'Anti-Rheb [Rheb 5D5]',
 'Anti-OX32 [OX32] monoclonal antibody',
 'Anti-CD72 [BU40]

In [950]:
antibodies_cleaned = set([re.sub(r'[()\[\]{}]', '', x.lower()) for x in antibodies])
with open('antibodies.txt', 'w') as f:
    for line in antibodies_cleaned:
        f.write(f"{line}\n")

In [951]:
supplement_req = requests.get(f'https://supplementrelief.com/numedica/')
supplement_soup = BeautifulSoup(supplement_req.content)
supplements = set([supp.get_text(strip=True).lower() for supp in supplement_soup.find_all("a", href=True)][12:625][:219])
with open('supplements.txt', 'w') as f:
    for line in supplements:
        f.write(f"{line}\n")

In [947]:
misc_req = requests.get(f'https://www.twentyeighthealth.com/sex-health-guide/types-of-insurance-cards')
misc_soup = BeautifulSoup(misc_req.content)
misc_labels = [x.get_text().split() for x in misc_soup.find_all("strong")][-1][6:10]
misc_labels.remove("or")
misc_labels_low = [m.lower().strip(',') for m in misc_labels]
misc_labels_low

['rxbin', 'rxpcn', 'rxgroup']

In [949]:
with open('medical_terms.txt', 'w') as f:
    for line in all_medical_terms+misc_labels_low:
        f.write(f"{line}\n")